![header](../figures/logos_partenaires._cmems_se.jpg)


<div class="alert alert-block alert-success">
<h1><center>Demo: Create and save mp4 movies of SWOT data  </center></h1></div>

***
**Authors:**  Datlas, IGE, IMEDEA & CLS <br>
**Copyright:** 2022 Datlas, IGE, IMEDEA & CLS <br>
**License:** MIT

In [1]:
import os
import glob
import sys
sys.path.append('..')
import numpy as np 
import xarray as xr 
import matplotlib.pyplot as plt
from datetime import datetime
import glob 

from src import mod_plot
from src import mod_switchvar
from src.dict_regions_info import *

In [2]:

region_info = RegionInfo('Cali_info').region_info   # Region dictionary info from dict_regions_info.py


<div class="alert alert-info" role="alert">

<h2>1. Read from regional data file </h2>

</div>
 

In [3]:
path_data = '../swot_data/V1.0.2_CALVAL/SWOT_L3_LR_SSH_Expert_Cali_v1.0.2.nc'

starting_date = np.datetime64('2023-05-01')

label_noisy = 'Noisy'   # Name for plots title and saving figures
label_denoised = 'Denoised'   # Name for plots title and saving figures


name_noisy = 'ssha_karin_2_edited' # Name of the denoised SWOT variable in the xarray file 
name_denoised = 'duacs_ssha_karin_2_filtered' # Name of the denoised SWOT variable in the xarray file

orbit = '1d'

ds_passes = xr.open_mfdataset(path_data,combine='nested',concat_dim='num_lines')
ds_passes

<xarray.Dataset>
Dimensions:                        (num_lines: 12804, num_pixels: 69)
Coordinates:
    longitude                      (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    latitude                       (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
Dimensions without coordinates: num_lines, num_pixels
Data variables: (12/13)
    distance_to_coast              (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    duacs_relative_vorticity       (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    duacs_speed_zonal              (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    duacs_speed_meridional         (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    duacs_ssha_karin_2_filtered    (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    time                           (num_lines, num_pixels) datetime64[ns] dask.array<chunksize=(12804, 69), meta=np.ndarray>
    ...                             ...
    swh_model                      (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    duacs_editing_flag             (num_lines, num_pixels) float32 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    ssha_karin_2_edited            (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    residuals                      (num_lines, num_pixels) float64 dask.array<chunksize=(12804, 69), meta=np.ndarray>
    cycle_number                   (num_lines) float32 dask.array<chunksize=(12804,), meta=np.ndarray>
    pass_number                    (num_lines) float32 dask.array<chunksize=(12804,), meta=np.ndarray>

<div class="alert alert-info" role="alert">

<h2>2. Create SSH movie </h2>

</div> 

In [4]:
mod_plot.movie_intercomp(ds_passes, methods=[label_noisy,label_denoised], var_type='ssh', name_var=[name_noisy,name_denoised],date=starting_date, dir_output='../figures/',
                    region=region_info['name'], vmax=0.2, suffix='v102', framerate=3, colsize = 14)

<div class="alert alert-info" role="alert">

<h2>3. Compute SSH gradients and Laplacian </h2>

</div>
 

In [5]:
grad_noisy, lapl_noisy = mod_switchvar.deriv1and2(ds_passes[name_noisy])
grad_denoised, lapl_denoised = mod_switchvar.deriv1and2(ds_passes[name_denoised])   

ds_passes = ds_passes.assign(grad_noisy=lambda ds_passes: ds_passes[name_noisy] * 0 + grad_noisy) 
ds_passes = ds_passes.assign(grad_denoised=lambda ds_passes: ds_passes[name_denoised] * 0 + grad_denoised) 

ds_passes = ds_passes.assign(lapl_noisy=lambda ds_passes: ds_passes[name_noisy] * 0 + lapl_noisy) 
ds_passes = ds_passes.assign(lapl_denoised=lambda ds_passes: ds_passes[name_denoised] * 0 + lapl_denoised) 


<div class="alert alert-info" role="alert">

<h2>4. Create SSH gradients and Laplacian movies </h2>

</div>
 

In [8]:
mod_plot.movie_intercomp(ds_passes, methods=[label_noisy,label_denoised], var_type='grad', name_var=['grad_noisy','grad_denoised'], date=starting_date, dir_output='../figures/',
                    region=region_info['name'], vmax=0.0002, suffix='v102', framerate=3, colsize = 14)

In [7]:
mod_plot.movie_intercomp(ds_passes, methods=[label_noisy,label_denoised], var_type='lapl', name_var=['lapl_noisy','lapl_denoised'], date=starting_date, dir_output='../figures/',
                    region=region_info['name'], vmax=0.003, suffix='v102', framerate=3, colsize = 14)